In [2]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go 
# floor = pd.read_csv("libFloor.csv")

In [3]:
floor = pd.read_csv("libFloor.csv")

In [4]:
### adding calendar day to libFloor data
from datetime import datetime
floor['Weekday'] = [datetime.strptime(dt, '%Y-%m-%d %H:%M:%S').strftime('%A') for dt in floor['Timestamp'].to_list()]

### converting hours
hour_convert = dict(
    { 0:'12 a.m.', 1:'1 a.m.', 2:'2 a.m.', 3:'3 a.m.', 4:'4 a.m.', 5:'5 a.m.',
      6:'6 a.m.', 7:'7 a.m.', 8:'8 a.m.', 9:'9 a.m.', 10:'10 a.m.', 11:'11 a.m.',
      12:'12 p.m.', 13:'1 p.m.', 14:'2 p.m.', 15:'3 p.m.', 16:'4 p.m.', 17:'5 p.m.', 
      18:'6 p.m.', 19:'7 p.m.', 20:'8 p.m.', 21:'9 p.m.', 22:'10 p.m.', 23:'11 p.m.'
})

floor['Hour Copy'] = floor['Hour'].map(hour_convert)
floor.head()


Location            Timestamp  Average Occupancy  Peak Occupancy  \
0     UCSB Library  2021-09-22 16:00:00                 12               2   
1  2nd Floor Ocean  2021-09-22 16:00:00                 12               2   
2        2nd Floor  2021-09-22 16:00:00                 12               2   
3     UCSB Library  2021-09-25 12:00:00                 30              39   
4  2nd Floor Ocean  2021-09-25 12:00:00                  3               4   

  Time Interval                                      Location Path  Hour  \
0         1hour                                UCSB > UCSB Library    16   
1         1hour  UCSB > UCSB Library > 2nd Floor > 2nd Floor Ocean    16   
2         1hour                    UCSB > UCSB Library > 2nd Floor    16   
3         1hour                                UCSB > UCSB Library    12   
4         1hour  UCSB > UCSB Library > 2nd Floor > 2nd Floor Ocean    12   

     Quarter    Weekday Hour Copy  
0  Fall 2021  Wednesday    4 p.m.  
1  Fall 2021  Wednesday    4 p.m.  
2  Fall 2021  Wednesday    4 p.m.  
3  Fall 2021   Saturday   12 p.m.  
4  Fall 2021   Saturday   12 p.m.

In [5]:
condition = floor['Location'] == 'UCSB Library'
### without UCSB Generalized Totals
clean_floor = floor[~condition]
### with UCSB Generalized Totals
floor_total = floor[condition]

floor_copy = floor
floor_copy = floor_copy[floor_copy['Quarter'].notna()]

quarters = floor_copy['Quarter'].unique().tolist()
# quarters.remove()
print(quarters)


['Fall 2021', 'Winter 2022', 'Spring 2022', 'Summer 2022', 'Fall 2022', 'Winter 2023', 'Spring 2023']


In [5]:
clean_floor.head()

Location            Timestamp  Average Occupancy  Peak Occupancy  \
1     2nd Floor Ocean  2021-09-22 16:00:00                 12               2   
2           2nd Floor  2021-09-22 16:00:00                 12               2   
4     2nd Floor Ocean  2021-09-25 12:00:00                  3               4   
5  2nd Floor Mountain  2021-09-25 12:00:00                  2               0   
6           2nd Floor  2021-09-25 12:00:00                  3               4   

  Time Interval                                      Location Path  Hour  \
1         1hour  UCSB > UCSB Library > 2nd Floor > 2nd Floor Ocean    16   
2         1hour                    UCSB > UCSB Library > 2nd Floor    16   
4         1hour  UCSB > UCSB Library > 2nd Floor > 2nd Floor Ocean    12   
5         1hour  UCSB > UCSB Library > 2nd Floor > 2nd Floor Mo...    12   
6         1hour                    UCSB > UCSB Library > 2nd Floor    12   

     Quarter    Weekday Hour Copy  
1  Fall 2021  Wednesday    4 p.m.  
2  Fall 2021  Wednesday    4 p.m.  
4  Fall 2021   Saturday   12 p.m.  
5  Fall 2021   Saturday   12 p.m.  
6  Fall 2021   Saturday   12 p.m.

### Histograms

In [7]:
floor_total = floor_total[floor_total['Quarter'].notna()]
floor_total["Hour Copy"] = floor_total['Hour'].map(hour_convert)
floor_total.sort_values(by='Hour')

fig = px.histogram(floor_total, x="Hour Copy", y="Average Occupancy", facet_col="Quarter")

fig.update_traces(marker_color='#f28e2c')

custom_hours = ['6 a.m.','3 p.m.']

fig.update_xaxes(title_text='', #"Hour", # remove reduntant x axis labels
                 tickangle=0,
                 tickvals=custom_hours,
                 ticktext=custom_hours, 
                 tickfont=dict(size=14, color='black', family="Arial"), 
                 categoryorder="array", 
                 categoryarray=[hour_convert[i] for i in range(24)])


fig.for_each_annotation(lambda a: a.update(text=a.text.split("=")[1]))

# removes facet= designation 
for axis in fig.layout:
    if type(fig.layout[axis]) == go.layout.YAxis:
        fig.layout[axis].title.text = ''
    if type(fig.layout[axis]) == go.layout.XAxis:
        fig.layout[axis].title.text = ''

fig.update_layout(
        # annotations used to remove 'boldness' created by stacked y axis labels
        annotations = list(fig.layout.annotations) + 
                    [go.layout.Annotation(
                            x=-0.07,
                            y=0.5,
                            font=dict(size=14, color = 'black'
                            ),
                            showarrow=False,
                            text="Total Visitors",
                            textangle=-90,
                            xref="paper",
                            yref="paper"
                        )
                    ], 
                    
        template="simple_white",
        title_font=dict(family="Arial", size=18, color='black'),
        title_text="Popular times of the week to visit the library by quarter and hour",
        font=dict(family="Arial", size=14, color='black'))

fig.show()

In [14]:
### Note 1: Quiet Floors are lumped into full floor 
### Note 2: GRS and Graduate Studies ommitted due to small values 
### The values are the cumulative sums of occupants through quarters Fall 2021 to Spring 2023

clean_floor['Location'] = clean_floor['Location'].str.replace(' - Quiet', '')
mask = clean_floor['Location'].str.contains('GRS|Graduate')
no_GRS = clean_floor[~mask]

floor_order = ["1st Floor", "1st Floor Mountain", "1st Floor Ocean", "Art & Architecture", 
               "2nd Floor", "2nd Floor Mountain", "2nd Floor Ocean", "4th Floor",
               "5th Floor", "6th Floor", "7th Floor", "8th Floor"]

fig = px.histogram(no_GRS, x="Hour Copy", y="Average Occupancy", facet_col="Location",
                    facet_col_wrap=4,
                    facet_row_spacing=0.1,
                    # overriding facet order using above list
                    category_orders={"Location":floor_order})

fig.update_yaxes(title_text="")
fig.update_traces(marker_color='#4e79a7')

custom_hours = ['3 a.m.','9 a.m.','3 p.m.','9 p.m.']

# renaming hour copy and properly ordering by aescending hour
# resolves issue with the misplacement of 4pm
fig.update_xaxes(title_text='', #"Hour", # remove reduntant x axis labels
                 tickangle=0,
                 tickvals=custom_hours,
                 ticktext=custom_hours, 
                 categoryorder="array", 
                 tickfont=dict(size=14, color='black', family="Arial"),\
                # resolves issue with the misplacement of 4pm
                 categoryarray=[hour_convert[i] for i in range(24)])

# removes facet= designation 
fig.for_each_annotation(lambda a: a.update(text=a.text.split("=")[1]))

for axis in fig.layout:
    if type(fig.layout[axis]) == go.layout.YAxis:
        fig.layout[axis].title.text = ''

fig.update_layout(
        # annotations used to remove 'boldness' created by stacked y axis labels
        annotations = list(fig.layout.annotations) + 
                    [go.layout.Annotation(
                            x=-0.07,
                            y=0.5,
                            font=dict(size=14, color = 'black'
                            ),
                            showarrow=False,
                            text="Total Visitors",
                            textangle=-90,
                            xref="paper",
                            yref="paper"
                        )
                    ],
        template="simple_white",
        title_font=dict(family="Arial", size=18, color='black'),
        title_text='Popular times of the week to visit the library by floor and hour',
        font=dict(family="Arial", size=14, color='black'))

fig.show()

/var/folders/5_/dpt6cl3j4fs4w5184wqyd8_r0000gn/T/ipykernel_26905/1660531232.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



### Heat Map

In [9]:
### Heat Map using mean visitors relative to week and hour instead of total

week_order = ["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]

# calculates the mean of 'Average Occupancy' based on 'Weekday' and 'Hour Copy'
mean = pd.pivot_table(floor_total, values='Average Occupancy', index='Weekday', columns='Hour Copy', aggfunc='mean')
mean = mean.reindex(week_order)

# Create heatmap using pandas pivot table from above 
fig = px.imshow(mean, x=mean.columns, y=mean.index,
                color_continuous_scale='portland')

custom_hours = ['12 a.m.','3 a.m.','6 a.m.','9 a.m.','12 p.m.','3 p.m.','6 p.m.','9 p.m.']

fig.update_yaxes(title_text="")

fig.update_xaxes(title_text='', 
                 tickangle=0,
                 tickvals=custom_hours,
                 ticktext=custom_hours, 
                 tickfont=dict(size=14, color='black', family="Arial"),
                 # used to reorder weeks
                 categoryorder="array", 
                 categoryarray=[hour_convert[i] for i in range(24)])

fig.update_layout(        
        template="simple_white",
        title_font=dict(family="Arial", size=18, color='black'),
        title_text='Popular times of the week to visit the library by day and hour',
        font=dict(family="Arial", size=14, color='black'),
        coloraxis_colorbar_title='Mean Visitors',
        coloraxis_colorbar=dict(
        title_font=dict(size=14, color='black'), 
        tickfont=dict(size=14)  # Adjust the font size here
    ))

# removes facet= designation 
fig.for_each_annotation(lambda a: a.update(text=a.text.split("=")[1]))
fig.show()

## Total Occupants by quarter
data courtesy of BOPS

In [10]:
d = {'Fall':[855539,811983,861807,859829,257,653655,668676], 
    'Winter':[755598,801348,854998,682275,241,324574,706988],
    'Spring': [768324,785782,820736,0,8082,598260,627746],
    'Summer':[262421,217676,248824,0,8528,194910,51835]}
year = pd.DataFrame(data=d)
year.index=['2016-2017', '2017-2018', '2018-2019', '2019-2020','2020-2021','2021-2022','2022-2023']
year

Fall  Winter  Spring  Summer
2016-2017  855539  755598  768324  262421
2017-2018  811983  801348  785782  217676
2018-2019  861807  854998  820736  248824
2019-2020  859829  682275       0       0
2020-2021     257     241    8082    8528
2021-2022  653655  324574  598260  194910
2022-2023  668676  706988  627746   51835

Combined entrance data courtesy of BOPS

In [11]:
d = {# 'Week':['Week 1','Week 2','Week 3','Week 4','Week 5','Week 6','Week 7','Week 8','Week 9','Week 10','Finals'],
     'Fall 2022':[68836,66758,71025,75001,66755,66758,59455,57670,18697,69687,48034],
     'Winter 2023':[40773,56133,69193,76033,72916,66498,57586,70623,67725,78450,51670],
     'Spring 2023':[40211,62957,57615,64136,60617,60953,57294,52955,48303,80109,42596]}
qt = pd.DataFrame(data=d)
qt.index = ['Week 1','Week 2','Week 3','Week 4','Week 5','Week 6','Week 7','Week 8','Week 9','Week 10','Finals']
qt

Fall 2022  Winter 2023  Spring 2023
Week 1       68836        40773        40211
Week 2       66758        56133        62957
Week 3       71025        69193        57615
Week 4       75001        76033        64136
Week 5       66755        72916        60617
Week 6       66758        66498        60953
Week 7       59455        57586        57294
Week 8       57670        70623        52955
Week 9       18697        67725        48303
Week 10      69687        78450        80109
Finals       48034        51670        42596

In [12]:
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import plotly.express as px
import numpy as np

colors = ['#4e79a7','#edc949','#e15759','#76b7b2']

# plotly
fig = px.histogram(qt, 
             x = qt.index, 
             y = [c for c in qt.columns],
             color_discrete_sequence = colors
             )

fig.update_xaxes(title_text="Weeks of the Quarter", title_font=dict(size=14, family="Arial"))
fig.update_yaxes(title_text="Total Visitors", title_font=dict(size=14, family="Arial"))

fig.update_layout(font=dict(family="Arial", size=14),
                  template="simple_white",
                  title_text="Total library visitors by week and quarter", 
                  title_font=dict(size=18, family="Arial"),
                  legend=dict(
                  title_text="Quarter",
                  title_font=dict(size=14),
                  font=dict(size=14))
                  )

fig.show()

In [13]:

colors = ['#4e79a7','#edc949','#e15759','#76b7b2']

# plotly
fig = px.bar(year, 
             x = year.index,
             y = [c for c in year.columns],
             color_discrete_sequence = colors
             )

fig.update_layout(font=dict(family="Arial", size=14),
                  template="simple_white",
                  title_text="Total library visitors by school year and quarter", 
                  title_font=dict(size=18, family="Arial"),
                  legend=dict(
                  title_text="Quarter",
                  title_font=dict(size=14),
                  font=dict(size=14)))

fig.update_xaxes(title_text="School Year", title_font=dict(size=14, family="Arial"))
fig.update_yaxes(title_text="Total Visitors", title_font=dict(size=14, family="Arial"))

fig.show()
